In [21]:
import pandas as pd
import numpy as np
import holoviews as hv
import hvplot
import hvplot.pandas

In [22]:
df = pd.read_csv('./data/20210218-fridges-water-heater-v3.csv',
                 index_col='time',
                 parse_dates=True)

In [23]:
df.drop(columns='#',inplace=True)
df.head()

well_pump  new_fridge  water_heater  old_fridge
time                                                                
2021-02-11 12:54:36      0.037       0.501         0.147       0.684
2021-02-11 12:55:36      0.037       0.501         0.122       0.684
2021-02-11 12:56:36      0.037       0.501         0.147       0.684
2021-02-11 12:57:36      0.073       0.501         0.098       0.684
2021-02-11 12:58:36      0.049       0.501         0.122       0.684

In [40]:
# Account for the 220V appliances that were measured off of only one side:

# On second thought - the current reading is correct, but It will get doubled (compared to 110V)
# automatically when i multiply by voltage to get power
# df.well_pump = df.well_pump * 2
# df.water_heater = df.water_heater * 2
df.head()

well_pump  new_fridge  water_heater  old_fridge  \
time                                                                   
2021-02-11 12:54:36      0.037       0.501         0.147       0.684   
2021-02-11 12:55:36      0.037       0.501         0.122       0.684   
2021-02-11 12:56:36      0.037       0.501         0.147       0.684   
2021-02-11 12:57:36      0.073       0.501         0.098       0.684   
2021-02-11 12:58:36      0.049       0.501         0.122       0.684   

                     new_fridge_wh  old_fridge_wh  water_heater_wh  \
time                                                                 
2021-02-11 12:54:36         0.9185          1.254         0.539000   
2021-02-11 12:55:36         0.9185          1.254         0.447333   
2021-02-11 12:56:36         0.9185          1.254         0.539000   
2021-02-11 12:57:36         0.9185          1.254         0.359333   
2021-02-11 12:58:36         0.9185          1.254         0.447333   

                     well_pump_wh  new_fridge_wh_accum  old_fridge_wh_accum  \
time                                                                          
2021-02-11 12:54:36      0.135667               0.9185                1.254   
2021-02-11 12:55:36      0.135667               1.8370                2.508   
2021-02-11 12:56:36      0.135667               2.7555                3.762   
2021-02-11 12:57:36      0.267667               3.6740                5.016   
2021-02-11 12:58:36      0.179667               4.5925                6.270   

                     water_heater_wh_accum  well_pump_wh_accum  
time                                                            
2021-02-11 12:54:36               0.539000            0.135667  
2021-02-11 12:55:36               0.986333            0.271333  
2021-02-11 12:56:36               1.525333            0.407000  
2021-02-11 12:57:36               1.884667            0.674667  
2021-02-11 12:58:36               2.332000            0.854333

In [25]:
# Start the data at xxxx once we know the data readers were in place
# df = df[df.index.values > pd.to_datetime('2021/02/10-4:30pm')]
df.hvplot.line()

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [26]:
staycation_start_line = hv.VLine(pd.to_datetime('2/12/2021-1pm'))
staycation_end_line = hv.VLine(pd.to_datetime('2/14/2021-1pm'))
staycation_start_line.opts(color='black', line_dash='dashed', line_width=1)    
staycation_end_line.opts(color='black', line_dash='dashed', line_width=1)    

df.drop(['water_heater','well_pump'],axis=1).hvplot.line() * staycation_start_line * staycation_end_line

:Overlay
   .NdOverlay.I :NdOverlay   [Variable]
      :Curve   [time]   (value)
   .VLine.I     :VLine   [x,y]
   .VLine.II    :VLine   [x,y]

In [27]:
df.drop(['new_fridge','old_fridge'],axis=1).hvplot.line() * staycation_start_line * staycation_end_line

:Overlay
   .NdOverlay.I :NdOverlay   [Variable]
      :Curve   [time]   (value)
   .VLine.I     :VLine   [x,y]
   .VLine.II    :VLine   [x,y]

In [28]:
# Convert to Whr's used
samples_per_hour = 60
fridge_voltage = 110
water_heater_voltage = 220
well_pump_voltage = 220



df['new_fridge_wh'] =   (df['new_fridge'] / samples_per_hour) * fridge_voltage
df['old_fridge_wh'] =   (df['old_fridge'] / samples_per_hour) * fridge_voltage
df['water_heater_wh'] = (df['water_heater'] / samples_per_hour) * water_heater_voltage
df['well_pump_wh'] = (df['well_pump'] / samples_per_hour) * well_pump_voltage

In [29]:

df['new_fridge_wh_accum'] =   df['new_fridge_wh'].cumsum()
df['old_fridge_wh_accum'] =   df['old_fridge_wh'].cumsum()
df['water_heater_wh_accum'] = df['water_heater_wh'].cumsum()
df['well_pump_wh_accum'] = df['well_pump_wh'].cumsum()



In [41]:
def plot_power_and_energy(df, scaling_factor=1):
    df['new_fridge_wh_accum'] =   df['new_fridge_wh_accum'] / scaling_factor
    df['old_fridge_wh_accum'] =   df['old_fridge_wh_accum'] / scaling_factor
    df['water_heater_wh_accum'] = df['water_heater_wh_accum'] / scaling_factor
    df['well_pump_wh_accum'] =    df['well_pump_wh_accum'] / scaling_factor
    
    plot = df.drop(['water_heater_wh_accum',
                    'water_heater_wh',
                   'well_pump_wh_accum',
                   'well_pump_wh'],axis=1).hvplot.line(width=900) * staycation_start_line * staycation_end_line
    
    df['new_fridge_wh_accum'] =   df['new_fridge_wh_accum'] * scaling_factor
    df['old_fridge_wh_accum'] =   df['old_fridge_wh_accum'] * scaling_factor
    df['water_heater_wh_accum'] = df['water_heater_wh_accum'] * scaling_factor
    df['well_pump_wh_accum'] =    df['well_pump_wh_accum'] * scaling_factor
    
    return plot

In [42]:
plot_power_and_energy(df.drop(['new_fridge',
                               'water_heater',
                               'old_fridge',
                               'well_pump'],axis=1),500) 

:Overlay
   .NdOverlay.I :NdOverlay   [Variable]
      :Curve   [time]   (value)
   .VLine.I     :VLine   [x,y]
   .VLine.II    :VLine   [x,y]

In [43]:
df_accum = df[['well_pump_wh_accum','water_heater_wh_accum','old_fridge_wh_accum','new_fridge_wh_accum']].copy()

In [44]:
df_accum

well_pump_wh_accum  water_heater_wh_accum  \
time                                                             
2021-02-11 12:54:36            0.135667               0.539000   
2021-02-11 12:55:36            0.271333               0.986333   
2021-02-11 12:56:36            0.407000               1.525333   
2021-02-11 12:57:36            0.674667               1.884667   
2021-02-11 12:58:36            0.854333               2.332000   
...                                 ...                    ...   
2021-02-18 13:38:36         4357.147667          110449.313333   
2021-02-18 13:39:36         4357.551000          110449.760667   
2021-02-18 13:40:36         4357.954333          110450.120000   
2021-02-18 13:41:36         4358.266000          110450.479333   
2021-02-18 13:42:36         4358.489667          110451.194333   

                     old_fridge_wh_accum  new_fridge_wh_accum  
time                                                           
2021-02-11 12:54:36             1.254000             0.918500  
2021-02-11 12:55:36             2.508000             1.837000  
2021-02-11 12:56:36             3.762000             2.755500  
2021-02-11 12:57:36             5.016000             3.674000  
2021-02-11 12:58:36             6.270000             4.592500  
...                                  ...                  ...  
2021-02-18 13:38:36          6573.523000         13559.463500  
2021-02-18 13:39:36          6573.792500         13560.493833  
2021-02-18 13:40:36          6573.972167         13561.524167  
2021-02-18 13:41:36          6574.195833         13562.530667  
2021-02-18 13:42:36          6574.239833         13563.537167  

[10129 rows x 4 columns]

In [45]:
df_accum.hvplot.line(grid=True)

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [46]:
df_orig = df[['well_pump_wh', 'water_heater_wh','old_fridge_wh','new_fridge_wh']]

In [47]:

df_orig_by_day = df_orig.resample('D').sum()
df_orig_by_day = df_orig_by_day[:-1]
df_orig_by_day = df_orig_by_day[1:]

In [48]:
df_orig_by_day.hvplot.line(grid=True)

:NdOverlay   [Variable]
   :Curve   [time]   (value)

In [49]:
# around 9 kWh / day for water heater

In [50]:
df_orig_by_day[2:].water_heater_wh.mean()

17860.736666666897